<a href="https://colab.research.google.com/github/tsimut/Final-Project/blob/master/topic_modelling.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
pip install spacy

In [2]:
pip install pyLDAvis

     |████████████████████████████████| 1.6MB 4.8MB/s 
  Stored in directory: /root/.cache/pip/wheels/98/71/24/513a99e58bb6b8465bae4d2d5e9dba8f0bef8179e3051ac414
Successfully built pyLDAvis


In [0]:
import nltk
from nltk import FreqDist
import pandas as pd
pd.set_option("display.max_colwidth", 200)
import numpy as np
import re
import spacy
import gensim
from gensim import corpora
import pyLDAvis
import pyLDAvis.gensim
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
from bs4 import BeautifulSoup
import requests
import time
import nltk
from nltk.corpus import stopwords

In [0]:
review=[]
rating=[]

In [5]:
#USE BEAUTIFUL SOUP TO SCRAPE REVIEWS FROM WEBSITE AND APPEND THE DATA TO LISTS
page_count = 0
while page_count <10:
    
    url = "https://www.consumeraffairs.com/finance/royal_bank.html?page=%s" %(page_count)
    page = requests.get(url)
    soup = BeautifulSoup(page.content, 'html.parser')
    reviews=soup.find(id="reviews-container")
    
    comments=soup.find_all("div", class_="rvw-bd ca-txt-bd-2")
    for ct in comments:
        review.append(ct.find("p").get_text())
    
    star=reviews.find_all("div",class_="rvw__hdr-stat") 
    for st in star:
        try:
            rating.append(st.find("img")["data-rating"])
        except:
            rating.append(print("none"))
       
    page_count += 1

none
none


In [6]:
len(rating)

300

In [7]:
Reviews = pd.DataFrame({
"Review":review,    
"Rating":rating
})


Reviews.head(20)

Review Rating
0   We met Ratna in June 2012 as we move to Calgary. At that time both just got our jobs. Somehow we had a dream to buy our own house in Calgary. We were new to this town and looking for someone to he...    5.0
1   I have found their staff to be extremely helpful. Having worked in many financial institutions I can honestly agree that customers are more likely to provide a bad review than take the time to wri...    4.0
2   We opened two accounts with RBC. Jamie ** of the Salmon Arm branch spent 3 hrs with us, first opening a savings account and then a US high interest US account. She was very patient and walked us t...    4.0
3   I have banked with RBC for 32 years, and was looking to consolidate debt. They told me that I probably wouldn't be able to get a home equity loan despite having at least 20% equity, and that a con...    1.0
4   What a POS these PVQa are. This idiotic piece of software has decided in its tiny brain that my computer is no longer recognised as secure and keeps bombarding me with these questions whenever I t...    1.0
5   Today I heard from the Manager.  He was exceptionally good and dealt with all my concerns.  He explained some of the reasons for the mishaps and how they will be rectified.  I feel very good about...   None
6   Hi my name is Fidi and I have been a client with RBC for over 8 years. I do not owe them money and my account always had funds. Last week I received a letter in the mail saying they're closing dow...    1.0
7   Extremely rude people work on the other end of the phone. There needs to be some serious government oversight because this company does many things that are totally unethical. They charge fees aft...    1.0
8   I've been a RBC client for nearly 20 years and recently switched my personal accounts to them from the credit union I have belonged to for nearly 40 years. Because I am a senior and can't always g...    2.0
9   Wow, I have never dealt with a more unprofessional business ever. I spent 1 hour on the phone with them and was preapproved for a loan. After waiting a few days for my appt I get a call 2 hours be...    1.0
10  Business owners stay away from this place. An hour long interview for a $5000 credit card and then tons of signatures. After 2 weeks I was again called back to bank to sign some more stupid papers...    1.0
11  The bank put a deposit only message on my account, I went into the branch on Monday to have it removed. I was told the manager would review my account the next morning and contact me by the end of...    1.0
12  I have a business account with RBC. I called them to request a line of credit. After wasting about an hour on the phone, the person I was talking to (he said his name is Jay) asked me to be on hol...    1.0
13  The franchising come with everything in a neat package. Then little by little they start revoke credit cards and lines of credit. When that doesn’t make you quite they close bank account send lett...    1.0
14  If RBC read any of these reviews they would have a better understanding that their customers DO NOT want virtual freaking customer service and wish to speak to a live person. Hire more people to d...    1.0
15  I have business account with RBC. Where I deposit cheques every month and all the cheques are from same one client! They been putting it on hold for 24 hours! Which was ok and now they started hol...    1.0
16  I applied for a mortgage at RBC. They advertise that their mortgage approval takes from 60 seconds to 3 hours. More than 2 weeks passed and they even didn't notify me that it was denied. So I've l...    1.0
17  I have been RBC client for over 12 years, with the good background history with good income. I tried to apply for any service such as personal loan and line of credit but I was denied. It is a sha...    1.0
18  I opened my account just recently at a branch in Dundas and Spadina last month. I plan to use it after a month, once I joined my next job at a new company. The advisor gave me a void c

In [0]:
Reviews = Reviews[Reviews.Rating.notnull()]

In [9]:
Reviews.index = range(len(Reviews.index))
Reviews

Review Rating
0    We met Ratna in June 2012 as we move to Calgary. At that time both just got our jobs. Somehow we had a dream to buy our own house in Calgary. We were new to this town and looking for someone to he...    5.0
1    I have found their staff to be extremely helpful. Having worked in many financial institutions I can honestly agree that customers are more likely to provide a bad review than take the time to wri...    4.0
2    We opened two accounts with RBC. Jamie ** of the Salmon Arm branch spent 3 hrs with us, first opening a savings account and then a US high interest US account. She was very patient and walked us t...    4.0
3    I have banked with RBC for 32 years, and was looking to consolidate debt. They told me that I probably wouldn't be able to get a home equity loan despite having at least 20% equity, and that a con...    1.0
4    What a POS these PVQa are. This idiotic piece of software has decided in its tiny brain that my computer is no longer recognised as secure and keeps bombarding me with these questions whenever I t...    1.0
5    Hi my name is Fidi and I have been a client with RBC for over 8 years. I do not owe them money and my account always had funds. Last week I received a letter in the mail saying they're closing dow...    1.0
6    Extremely rude people work on the other end of the phone. There needs to be some serious government oversight because this company does many things that are totally unethical. They charge fees aft...    1.0
7    I've been a RBC client for nearly 20 years and recently switched my personal accounts to them from the credit union I have belonged to for nearly 40 years. Because I am a senior and can't always g...    2.0
8    Wow, I have never dealt with a more unprofessional business ever. I spent 1 hour on the phone with them and was preapproved for a loan. After waiting a few days for my appt I get a call 2 hours be...    1.0
9    Business owners stay away from this place. An hour long interview for a $5000 credit card and then tons of signatures. After 2 weeks I was again called back to bank to sign some more stupid papers...    1.0
10   The bank put a deposit only message on my account, I went into the branch on Monday to have it removed. I was told the manager would review my account the next morning and contact me by the end of...    1.0
11   I have a business account with RBC. I called them to request a line of credit. After wasting about an hour on the phone, the person I was talking to (he said his name is Jay) asked me to be on hol...    1.0
12   The franchising come with everything in a neat package. Then little by little they start revoke credit cards and lines of credit. When that doesn’t make you quite they close bank account send lett...    1.0
13   If RBC read any of these reviews they would have a better understanding that their customers DO NOT want virtual freaking customer service and wish to speak to a live person. Hire more people to d...    1.0
14   I have business account with RBC. Where I deposit cheques every month and all the cheques are from same one client! They been putting it on hold for 24 hours! Which was ok and now they started hol...    1.0
15   I applied for a mortgage at RBC. They advertise that their mortgage approval takes from 60 seconds to 3 hours. More than 2 weeks passed and they even didn't notify me that it was denied. So I've l...    1.0
16   I have been RBC client for over 12 years, with the good background history with good income. I tried to apply for any service such as personal loan and line of credit but I was denied. It is a sha...    1.0
17   I opened my account just recently at a branch in Dundas and Spadina last month. I plan to use it after a month, once I joined my next job at a new company. The advisor gave me a void cheque for th...    1.0
18   Fraudsters and scammer who steal credit cards work with RBC employees and inside people on RBC to allow high-risk transactions, RBC failed to flag 2 transactions for

In [0]:
Sentiments=[]
for i in Reviews["Rating"]:
  x=float(i)
  if x <4:
    Sentiments.append("N")
  else:
    Sentiments.append("P")

In [11]:
Reviews['Sentiments'] = Sentiments
Reviews.head(20)

Review  ... Sentiments
0   We met Ratna in June 2012 as we move to Calgary. At that time both just got our jobs. Somehow we had a dream to buy our own house in Calgary. We were new to this town and looking for someone to he...  ...          P
1   I have found their staff to be extremely helpful. Having worked in many financial institutions I can honestly agree that customers are more likely to provide a bad review than take the time to wri...  ...          P
2   We opened two accounts with RBC. Jamie ** of the Salmon Arm branch spent 3 hrs with us, first opening a savings account and then a US high interest US account. She was very patient and walked us t...  ...          P
3   I have banked with RBC for 32 years, and was looking to consolidate debt. They told me that I probably wouldn't be able to get a home equity loan despite having at least 20% equity, and that a con...  ...          N
4   What a POS these PVQa are. This idiotic piece of software has decided in its tiny brain that my computer is no longer recognised as secure and keeps bombarding me with these questions whenever I t...  ...          N
5   Hi my name is Fidi and I have been a client with RBC for over 8 years. I do not owe them money and my account always had funds. Last week I received a letter in the mail saying they're closing dow...  ...          N
6   Extremely rude people work on the other end of the phone. There needs to be some serious government oversight because this company does many things that are totally unethical. They charge fees aft...  ...          N
7   I've been a RBC client for nearly 20 years and recently switched my personal accounts to them from the credit union I have belonged to for nearly 40 years. Because I am a senior and can't always g...  ...          N
8   Wow, I have never dealt with a more unprofessional business ever. I spent 1 hour on the phone with them and was preapproved for a loan. After waiting a few days for my appt I get a call 2 hours be...  ...          N
9   Business owners stay away from this place. An hour long interview for a $5000 credit card and then tons of signatures. After 2 weeks I was again called back to bank to sign some more stupid papers...  ...          N
10  The bank put a deposit only message on my account, I went into the branch on Monday to have it removed. I was told the manager would review my account the next morning and contact me by the end of...  ...          N
11  I have a business account with RBC. I called them to request a line of credit. After wasting about an hour on the phone, the person I was talking to (he said his name is Jay) asked me to be on hol...  ...          N
12  The franchising come with everything in a neat package. Then little by little they start revoke credit cards and lines of credit. When that doesn’t make you quite they close bank account send lett...  ...          N
13  If RBC read any of these reviews they would have a better understanding that their customers DO NOT want virtual freaking customer service and wish to speak to a live person. Hire more people to d...  ...          N
14  I have business account with RBC. Where I deposit cheques every month and all the cheques are from same one client! They been putting it on hold for 24 hours! Which was ok and now they started hol...  ...          N
15  I applied for a mortgage at RBC. They advertise that their mortgage approval takes from 60 seconds to 3 hours. More than 2 weeks passed and they even didn't notify me that it was denied. So I've l...  ...          N
16  I have been RBC client for over 12 years, with the good background history with good income. I tried to apply for any service such as personal loan and line of credit but I was denied. It is a sha...  ...          N
17  I opened my account just recently at a branch in Dundas and Spadina last month. I plan to use it after a month, once I joined my next job at a new company. The advisor gave me a void cheque for th...  ...          N
18  Fraudsters an

In [0]:
# remove unwanted characters, numbers and symbols
Reviews['Clean Reviews'] = Reviews['Review'].str.replace("[^a-zA-Z#]", " ")

In [13]:
Reviews

Review  ...                                                                                                                                                                                            Clean Reviews
0    We met Ratna in June 2012 as we move to Calgary. At that time both just got our jobs. Somehow we had a dream to buy our own house in Calgary. We were new to this town and looking for someone to he...  ...  We met Ratna in June      as we move to Calgary  At that time both just got our jobs  Somehow we had a dream to buy our own house in Calgary  We were new to this town and looking for someone to he...
1    I have found their staff to be extremely helpful. Having worked in many financial institutions I can honestly agree that customers are more likely to provide a bad review than take the time to wri...  ...  I have found their staff to be extremely helpful  Having worked in many financial institutions I can honestly agree that customers are more likely to provide a bad review than take the time to wri...
2    We opened two accounts with RBC. Jamie ** of the Salmon Arm branch spent 3 hrs with us, first opening a savings account and then a US high interest US account. She was very patient and walked us t...  ...  We opened two accounts with RBC  Jamie    of the Salmon Arm branch spent   hrs with us  first opening a savings account and then a US high interest US account  She was very patient and walked us t...
3    I have banked with RBC for 32 years, and was looking to consolidate debt. They told me that I probably wouldn't be able to get a home equity loan despite having at least 20% equity, and that a con...  ...  I have banked with RBC for    years  and was looking to consolidate debt  They told me that I probably wouldn t be able to get a home equity loan despite having at least     equity  and that a con...
4    What a POS these PVQa are. This idiotic piece of software has decided in its tiny brain that my computer is no longer recognised as secure and keeps bombarding me with these questions whenever I t...  ...  What a POS these PVQa are  This idiotic piece of software has decided in its tiny brain that my computer is no longer recognised as secure and keeps bombarding me with these questions whenever I t...
5    Hi my name is Fidi and I have been a client with RBC for over 8 years. I do not owe them money and my account always had funds. Last week I received a letter in the mail saying they're closing dow...  ...  Hi my name is Fidi and I have been a client with RBC for over   years  I do not owe them money and my account always had funds  Last week I received a letter in the mail saying they re closing dow...
6    Extremely rude people work on the other end of the phone. There needs to be some serious government oversight because this company does many things that are totally unethical. They charge fees aft...  ...  Extremely rude people work on the other end of the phone  There needs to be some serious government oversight because this company does many things that are totally unethical  They charge fees aft...
7    I've been a RBC client for nearly 20 years and recently switched my personal accounts to them from the credit union I have belonged to for nearly 40 years. Because I am a senior and can't always g...  ...  I ve been a RBC client for nearly    years and recently switched my personal accounts to them from the credit union I have belonged to for nearly    years  Because I am a senior and can t always g...
8    Wow, I have never dealt with a more unprofessional business ever. I spent 1 hour on the phone with them and was preapproved for a loan. After waiting a few days for my appt I get a call 2 hours be...  ...  Wow  I have never dealt with a more unprofessional business ever  I spent   hour on the phone with them and was preapproved for a loan  After waiting a few days for my appt I get a call   hours be...
9    Business owners stay away from this place. An hour long interview for a $5000 credi

In [0]:
Reviews['Clean Reviews'] = Reviews['Clean Reviews'].apply(lambda x: " ".join(x.lower() for x in x.split()))

In [15]:
# remove short words (length < 3)
Reviews['Clean Reviews'] = Reviews['Clean Reviews'].apply(lambda x: ' '.join([w for w in x.split() if len(w)>2]))

Reviews['Clean Reviews'].head()

0    met ratna june move calgary that time both just got our jobs somehow had dream buy our own house calgary were new this town and looking for someone help buying house already had account rbc just g...
1    have found their staff extremely helpful having worked many financial institutions can honestly agree that customers are more likely provide bad review than take the time write good review when wa...
2    opened two accounts with rbc jamie the salmon arm branch spent hrs with first opening savings account and then high interest account she was very patient and walked through online banking explaini...
3    have banked with rbc for years and was looking consolidate debt they told that probably wouldn able get home equity loan despite having least equity and that consolidation loan would not save much...
4    what pos these pvqa are this idiotic piece software has decided its tiny brain that computer longer recognised secure and keeps bombarding with these questions whenever try si

In [16]:
import nltk
nltk.download('stopwords')
stop = stopwords.words('english')
Reviews['Clean Reviews'] = Reviews['Clean Reviews'].apply(lambda x: " ".join(x for x in x.split() if x not in stop))
Reviews['Clean Reviews']

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


0      met ratna june move calgary time got jobs somehow dream buy house calgary new town looking someone help buying house already account rbc gave call customer service referred ratna name met person e...
1      found staff extremely helpful worked many financial institutions honestly agree customers likely provide bad review take time write good review warranted dealt royal bank past found staff offered ...
2      opened two accounts rbc jamie salmon arm branch spent hrs first opening savings account high interest account patient walked online banking explaining every step detailed user friendly manner expl...
3      banked rbc years looking consolidate debt told probably able get home equity loan despite least equity consolidation loan would save much money suggested apply visa balance transfer months may get...
4      pos pvqa idiotic piece software decided tiny brain computer longer recognised secure keeps bombarding questions whenever try sign truly disgusting worst security sof

In [17]:
#IDENTIFY TOP 10 OCCURING WORDS
freq = pd.Series(' '.join(Reviews['Clean Reviews']).split()).value_counts()[:10]
freq

rbc        402
bank       368
account    295
credit     179
money      135
years      127
told       123
get        117
branch     114
card       113
dtype: int64

In [0]:
common_word=("rbc","told","get","bank","banking","royal","years","money","account")

def remove_commonwords(rev):
    rev_new = " ".join([i for i in rev if i not in common_word])
    return rev_new


In [19]:
least = pd.Series(' '.join(Reviews['Clean Reviews']).split()).value_counts()[-10:]
least

wondered      1
mostly        1
management    1
doubling      1
disputed      1
ppl           1
paypal        1
anyhow        1
exposed       1
reference     1
dtype: int64

In [0]:
least = list(least.index)
Reviews['Clean Reviews'] = Reviews['Clean Reviews'].apply(lambda x: " ".join(x for x in x.split() if x not in least))

In [21]:

Reviews['Clean Reviews'] = Reviews['Clean Reviews'].apply(lambda x: " ".join(x for x in x.split() if x not in common_word))
Reviews['Clean Reviews'].head()

0    met ratna june move calgary time got jobs somehow dream buy house calgary new town looking someone help buying house already gave call customer service referred ratna name met person expressed des...
1    found staff extremely helpful worked many financial institutions honestly agree customers likely provide bad review take time write good review warranted dealt past found staff offered products su...
2    opened two accounts jamie salmon arm branch spent hrs first opening savings high interest patient walked online explaining every step detailed user friendly manner explained various services costs...
3    banked looking consolidate debt probably able home equity loan despite least equity consolidation loan would save much suggested apply visa balance transfer months may high enough limit help asked...
4    pos pvqa idiotic piece software decided tiny brain computer longer recognised secure keeps bombarding questions whenever try sign truly disgusting worst security software big 

In [0]:
import spacy
nlp = spacy.load('en', disable=['parser', 'ner'])

# function to lemmatize text
def lemmatization(texts):
    output = []
    for i in texts:
        s = [token.lemma_ for token in nlp(i)]
        output.append(' '.join(s))
    return output

In [0]:
Reviews['Clean Reviews'] = lemmatization(Reviews['Clean Reviews'])

In [24]:
Reviews

Review  ...                                                                                                                                                                                            Clean Reviews
0    We met Ratna in June 2012 as we move to Calgary. At that time both just got our jobs. Somehow we had a dream to buy our own house in Calgary. We were new to this town and looking for someone to he...  ...  meet ratna june move calgary time get job somehow dream buy house calgary new town look someone help buy house already give call customer service refer ratna name meet person express desire buy ne...
1    I have found their staff to be extremely helpful. Having worked in many financial institutions I can honestly agree that customers are more likely to provide a bad review than take the time to wri...  ...  find staff extremely helpful work many financial institution honestly agree customer likely provide bad review take time write good review warrant deal past find staff offer product suit need make...
2    We opened two accounts with RBC. Jamie ** of the Salmon Arm branch spent 3 hrs with us, first opening a savings account and then a US high interest US account. She was very patient and walked us t...  ...  open two account jamie salmon arm branch spend hrs first open saving high interest patient walk online explain every step detail user friendly manner explain various service cost disadvantage adva...
3    I have banked with RBC for 32 years, and was looking to consolidate debt. They told me that I probably wouldn't be able to get a home equity loan despite having at least 20% equity, and that a con...  ...  bank look consolidate debt probably able home equity loan despite least equity consolidation loan would save much suggest apply visa balance transfer month may high enough limit help ask sure say ...
4    What a POS these PVQa are. This idiotic piece of software has decided in its tiny brain that my computer is no longer recognised as secure and keeps bombarding me with these questions whenever I t...  ...  pos pvqa idiotic piece software decide tiny brain computer longer recognise secure keep bombard question whenever try sign truly disgusting bad security software big matter canadian guy deal bell ...
5    Hi my name is Fidi and I have been a client with RBC for over 8 years. I do not owe them money and my account always had funds. Last week I received a letter in the mail saying they're closing dow...  ...  name fidi client owe always fund last week receive letter mail say closing call every department tell release information regard want tell recommend go anyone whether line credit anything else clo...
6    Extremely rude people work on the other end of the phone. There needs to be some serious government oversight because this company does many things that are totally unethical. They charge fees aft...  ...  extremely rude people work end phone need serious government oversight company many thing totally unethical charge fee service cancel second call cancel fee clearly literally people look statement...
7    I've been a RBC client for nearly 20 years and recently switched my personal accounts to them from the credit union I have belonged to for nearly 40 years. Because I am a senior and can't always g...  ...  client nearly recently switch personal account credit union belong nearly senior always branch rely line service pay bill manage account say line service encounter business seem bad record half ti...
8    Wow, I have never dealt with a more unprofessional business ever. I spent 1 hour on the phone with them and was preapproved for a loan. After waiting a few days for my appt I get a call 2 hours be...  ...                        wow never deal unprofessional business ever spend hour phone preapprove loan wait day appt call hour tell person approve new help wait switch everything another would better one
9    Business owners stay away from this place. An hour long interview for a $5000 credi

In [0]:
import tensorflow_hub as hub
import tensorflow as tf

elmo = hub.Module("https://tfhub.dev/google/elmo/2", trainable=True)

In [0]:
def elmo_vectors(x):
  embeddings = elmo(x, signature="default", as_dict=True)["elmo"]

  with tf.Session() as sess:
    sess.run(tf.global_variables_initializer())
    sess.run(tf.tables_initializer())
    # return average of ELMo features
    return sess.run(tf.reduce_mean(embeddings,1))

In [0]:
from sklearn.model_selection import train_test_split

train, test = train_test_split(Reviews['Clean Reviews'], test_size=0.2)

In [0]:
df1=train.tolist()
df2=test.tolist()

In [33]:
elmo_test=[]
print (len(df2))
for i in range(len(df2)):
    elmo_test.append(elmo_vectors([df2[i]])[0])

60


In [34]:
elmo_train=[]
print (len(df1))
for i in range(len(df1)):
    print (df1[i])
    elmo_train.append(elmo_vectors([df1[i]])[0])
   

238


KeyboardInterrupt: ignored

In [35]:
len(elmo_train)

230

In [0]:
reviews = [remove_commonwords(r.split()) for r in Reviews['Clean Reviews']]

In [40]:
reviews

['met ratna june move calgary time got jobs somehow dream buy house calgary new town looking someone help buying house already gave call customer service referred ratna name met person expressed desire buy new house nice asked four pay stubs processed mortgage pre approval says wait another three months become permanent status employment',
 'found staff extremely helpful worked many financial institutions honestly agree customers likely provide bad review take time write good review warranted dealt past found staff offered products suited needs made suggestions even ask wealthy perfect credit',
 'opened two accounts jamie salmon arm branch spent hrs first opening savings high interest patient walked online explaining every step detailed user friendly manner explained various services costs disadvantages advantages friendly professional manner departed client cards canadian mastercard high interest savings visa card applications deposited monies accounts travel every spring arizona reli

In [0]:
nlp = spacy.load('en', disable=['parser', 'ner'])

def lemmatization(texts, tags=['NOUN', 'ADJ']):
  output = []
  for sent in texts:
    doc = nlp(" ".join(sent)) 
    output.append([token.lemma_ for token in doc if token.pos_ in tags])
  return output


In [0]:
tokenized_reviews = pd.Series(reviews).apply(lambda x: x.split())

In [0]:
lemma_reviews= lemmatization(tokenized_reviews)

In [44]:
lemma_reviews

[['ratna',
  'june',
  'calgary',
  'time',
  'job',
  'house',
  'calgary',
  'new',
  'town',
  'someone',
  'help',
  'house',
  'call',
  'customer',
  'service',
  'ratna',
  'name',
  'person',
  'desire',
  'new',
  'house',
  'nice',
  'pay',
  'stub',
  'mortgage',
  'pre',
  'approval',
  'month',
  'permanent',
  'status',
  'employment'],
 ['staff',
  'helpful',
  'many',
  'financial',
  'institution',
  'customer',
  'bad',
  'review',
  'time',
  'good',
  'review',
  'past',
  'staff',
  'product',
  'need',
  'suggestion',
  'wealthy',
  'perfect',
  'credit'],
 ['account',
  'jamie',
  'salmon',
  'arm',
  'branch',
  'hrs',
  'first',
  'saving',
  'high',
  'interest',
  'patient',
  'step',
  'user',
  'friendly',
  'manner',
  'various',
  'service',
  'cost',
  'advantage',
  'friendly',
  'professional',
  'manner',
  'client',
  'card',
  'canadian',
  'mastercard',
  'high',
  'interest',
  'saving',
  'visa',
  'card',
  'application',
  'monie',
  'account',

In [45]:
from gensim.models import Phrases
bigram = Phrases(lemma_reviews, min_count=3)
for idx in range(len(lemma_reviews)):
    for token in bigram[lemma_reviews[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            lemma_reviews[idx].append(token)

/usr/local/lib/python3.6/dist-packages/gensim/models/phrases.py:598: UserWarning: For a faster implementation, use the gensim.models.phrases.Phraser class
  warnings.warn("For a faster implementation, use the gensim.models.phrases.Phraser class")


In [0]:
#Remove rare and common tokens.

from gensim.corpora import Dictionary

# Create a dictionary representation of the documents.
dictionary = Dictionary(lemma_reviews)

# Filter out words that occur less than 20 documents, or more than 50% of the documents.
#dictionary.filter_extremes(no_below=20, no_above=0.5)

In [0]:
# Vectorize data.

# Bag-of-words representation of the documents.
corpus = [dictionary.doc2bow(doc) for doc in lemma_reviews]


In [48]:
corpus

[[(0, 1),
  (1, 2),
  (2, 1),
  (3, 1),
  (4, 1),
  (5, 1),
  (6, 1),
  (7, 1),
  (8, 3),
  (9, 1),
  (10, 1),
  (11, 1),
  (12, 1),
  (13, 1),
  (14, 2),
  (15, 1),
  (16, 1),
  (17, 1),
  (18, 1),
  (19, 1),
  (20, 2),
  (21, 1),
  (22, 1),
  (23, 1),
  (24, 1),
  (25, 1),
  (26, 1)],
 [(3, 1),
  (25, 1),
  (27, 1),
  (28, 1),
  (29, 1),
  (30, 1),
  (31, 1),
  (32, 1),
  (33, 1),
  (34, 1),
  (35, 1),
  (36, 1),
  (37, 1),
  (38, 1),
  (39, 2),
  (40, 2),
  (41, 1),
  (42, 1)],
 [(21, 1),
  (29, 1),
  (36, 1),
  (43, 2),
  (44, 1),
  (45, 1),
  (46, 1),
  (47, 1),
  (48, 1),
  (49, 1),
  (50, 2),
  (51, 1),
  (52, 1),
  (53, 1),
  (54, 1),
  (55, 1),
  (56, 2),
  (57, 2),
  (58, 2),
  (59, 1),
  (60, 2),
  (61, 2),
  (62, 2),
  (63, 1),
  (64, 1),
  (65, 1),
  (66, 1),
  (67, 1),
  (68, 2),
  (69, 1),
  (70, 1),
  (71, 1),
  (72, 1),
  (73, 1),
  (74, 1)],
 [(7, 1),
  (11, 1),
  (45, 1),
  (48, 1),
  (57, 1),
  (74, 1),
  (75, 1),
  (76, 1),
  (77, 1),
  (78, 1),
  (79, 1),
  (80, 2

In [51]:
# Creating the object for LDA model using gensim library
LDA = gensim.models.ldamodel.LdaModel
# Build LDA model
lda_model = LDA(corpus=corpus, id2word=dictionary, num_topics=4, random_state=100,
                chunksize=1000, passes=50)

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for

In [52]:
lda_model.print_topics()

[(0,
  '0.021*"mortgage" + 0.018*"card" + 0.016*"payment" + 0.015*"business" + 0.013*"credit" + 0.010*"new" + 0.009*"company" + 0.009*"credit_card" + 0.009*"day" + 0.009*"car"'),
 (1,
  '0.019*"time" + 0.016*"check" + 0.016*"service" + 0.014*"branch" + 0.013*"day" + 0.013*"cheque" + 0.012*"pay" + 0.012*"fund" + 0.011*"customer" + 0.010*"teller"'),
 (2,
  '0.021*"credit" + 0.021*"card" + 0.016*"month" + 0.016*"branch" + 0.014*"customer" + 0.012*"mortgage" + 0.011*"credit_card" + 0.011*"time" + 0.010*"service" + 0.010*"manager"'),
 (3,
  '0.031*"credit" + 0.019*"loan" + 0.017*"line" + 0.014*"branch" + 0.013*"time" + 0.011*"interest" + 0.011*"line_credit" + 0.010*"fee" + 0.010*"rate" + 0.009*"business"')]

In [53]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, dictionary)
vis

/usr/local/lib/python3.6/dist-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1     -0.104323  0.030228       1        1  29.171843
2     -0.025142  0.019838       2        1  25.969782
0      0.026452 -0.115068       3        1  25.883642
3      0.103013  0.065001       4        1  18.974735, topic_info=    Category        Freq         Term       Total  loglift  logprob
516  Default   44.000000        check   44.000000  30.0000  30.0000
237  Default   33.000000       cheque   33.000000  29.0000  29.0000
12   Default   84.000000     mortgage   84.000000  28.0000  28.0000
87   Default   60.000000         loan   60.000000  27.0000  27.0000
28   Default  149.000000       credit  149.000000  26.0000  26.0000
134  Default   54.000000         line   54.000000  25.0000  25.0000
135  Default   26.000000  line_credit   26.000000  24.0000  24.0000
384  Default   22.000000         rate   22.000000  23.0000  23.0000
195  Default   33.000000      deposit   33.000000  22.0000  22.0000
521  Default   29.000000       teller   29.000000  21.0000  21.0000
45   Default   19.000000  application   19.000000  20.0000  20.0000
50   Default  115.000000         card  115.000000  19.0000  19.0000
130  Default   41.000000         fund   41.000000  18.0000  18.0000
21   Default   71.000000      service   71.000000  17.0000  17.0000
8    Default   20.000000        house   20.000000  16.0000  16.0000
324  Default   72.000000      payment   72.000000  15.0000  15.0000
312  Default   30.000000          car   30.000000  14.0000  14.0000
48   Default  101.000000       branch  101.000000  13.0000  13.0000
148  Default   43.000000          fee   43.000000  12.0000  12.0000
60   Default   40.000000     interest   40.000000  11.0000  11.0000
144  Default   41.000000      company   41.000000  10.0000  10.0000
9    Default   19.000000          job   19.000000   9.0000   9.0000
29   Default   24.000000    financial   24.000000   8.0000   8.0000
131  Default   22.000000  information   22.000000   7.0000   7.0000
499  Default   30.000000    insurance   30.000000   6.0000   6.0000
142  Default   72.000000     business   72.000000   5.0000   5.0000
182  Default   57.000000  credit_card   57.000000   4.0000   4.0000
387  Default   10.000000         date   10.000000   3.0000   3.0000
159  Default   13.000000    statement   13.000000   2.0000   2.0000
14   Default   45.000000          new   45.000000   1.0000   1.0000
..       ...         ...          ...         ...      ...      ...
60    Topic4   18.939152     interest   40.401772   0.9044  -4.4801
28    Topic4   52.217567       credit  149.138824   0.6126  -3.4659
148   Topic4   17.361256          fee   43.851368   0.7355  -4.5671
322   Topic4    5.814487      monthly    9.822018   1.1378  -5.6610
366   Topic4    4.221600     december    6.551272   1.2226  -5.9811
31    Topic4   14.652476         good   44.010677   0.5622  -4.7367
341   Topic4    5.631676        right   10.699462   1.0203  -5.6929
259   Topic4    4.105035        waste    6.539192   1.1965  -6.0091
83    Topic4   10.998520         home   30.660320   0.6369  -5.0236
48    Topic4   22.696623       branch  101.125221   0.1679  -4.2991
76    Topic4    7.991305      balance   19.010128   0.7954  -5.3430
80    Topic4    9.638447         debt   27.346478   0.6192  -5.1556
25    Topic4   21.375202         time  112.262283   0.0035  -4.3591
144   Topic4   11.820092      company   41.552185   0.4049  -4.9516
142   Topic4   15.660213     business   72.574417   0.1286  -4.6702
29    Topic4    8.444548    financial   24.038528   0.6159  -5.2878
74    Topic4    9.925313         visa   34.051254   0.4293  -5.1263
33    Topic4    5.770858  institution   11.547323   0.9684  -5.6685
231   Topic4    8.599513        issue   29.137352   0.4417  -5.2696
118   Topic4   10.757488      manager   48.368965   0.1588  -5.0458
712   Topic4    5.466725         move   10.692871   0.9912  -5.7227
3     Topic4   12.560624     

In [0]:
import pickle

In [0]:
filename = 'finalized_model.sav'
pickle.dump(lda_model, open(filename, 'wb'))

In [0]:
from google.colab import drive
drive.mount('/content/drive')

In [0]:
!ls /content/gdrive/My Drive

ls: cannot access '/content/gdrive/My': No such file or directory
ls: cannot access 'Drive': No such file or directory


In [0]:
model_save_name = lda_model

In [0]:
!pip install -q torch==1.1.0 torchvision

In [0]:
import torch

In [0]:
path = F"/content/gdrive/My Drive/{model_save_name}" 
torch.save(lda_model, path)

In [0]:
model


In [0]:
name_dict = {   0: "Issues with Route", # 1 on the chart
                1: "Issues with payment/refund",    # 2 on the chart
                2: "Issues with time",  # 3 on the chart
            }

In [0]:
scored = model[doc_term_matrix]


In [0]:
topic_prob = map(lambda x: max(x, key=lambda item: item[1]), scored)
scored_reviews = pd.DataFrame(zip(reviews, topic_prob), columns=['Review', 'Main_Topic'])
scored_reviews[['Topic', 'Prob']] = scored_reviews['Main_Topic'].apply(pd.Series)
scored_reviews['Topic Name'] = scored_reviews['Topic'].map(name_dict)

In [0]:
scored_reviews

Review  ...                  Topic Name
0    great experiences couple bad experiences worst experience picked emergency situation needed hospital visit someone hurry already highway realized reeked alcohol completely intoxicated weaving lane...  ...  Issues with payment/refund
1    never lyft cab company highly ineffective oddly enough attracted highly qualified polite earn extra money enjoy scheduling simple smartphone application detects local via gps directs closest avail...  ...            Issues with time
2    never negative experience one downloaded first college one continue past years experiences better others opinion probably worse experience rides enjoyed ones respected privacy acted courteously pr...  ...  Issues with payment/refund
3    always skeptical rideshare services news reports assaults robberies company first time earlier year trip conference las vegas first excellent completed without problem second little scary requeste...  ...            Issues with time
4    several times far happy company easy set account love constantly upgrading features company making customer feel safe taking arrive timely manner professional love add feature signals letting know...  ...  Issues with payment/refund
5    trip last years overall rating excellent riders reviews account time call customer support team problems expect ever listen last week rider vomited peed inside vehicle refused send cleaning fee ta...  ...            Issues with time
6                           first time called says make cancel wont charged cancelled charged horse richland miss jackson miss area told cancel like take job could make dollars nothing piece nissan altima  ...            Issues with time
7                           lip service term quality india large number cars dirty acs hardly fictional trying defraud overcharge customer support india dismal overcharge rupees offered refund rupees joke  ...           Issues with Route
8    requested fort worth south henderson street irving texas upfront fare showed economy said offer max per discount aashish toyota corolla came literally said going home got exactly close home conven...  ...           Issues with Route
9                         earlier great provide prompt customer service quick redressal issues person speak acknowledgement even complain random multiple charges deducted trip thank god ola otherwise scam  ...  Issues with payment/refund
10   rider good passenger rating never issues experience general good month ago disabled account reached customer support email exchanges customer support sent rude offensive email violated terms condi...  ...  Issues with payment/refund
11                                             eats cancel order without refund ubereats friends order food eats money deliver food experience story customer support resolve problem delivery boy come home  ...            Issues with time
12   took igt sector noida shows rent approx premier looks good reached location without stoppage asked pay rupees totally disappointing prepaid taxi outside airport even charging rupees cross checked ...  ...            Issues with time
13   husband thought let everybody know experience new orleans never take went vacation new orleans take cruise arrived day suggestion travel agent make sure nothing went wrong new comfort inn suites n...  ...  Issues with payment/refund
14   montreal last week raining wanted quick destination booked amount displayed included surge mind running late wanted destination time unfortunately event taking place location cops blocked roads du...  ...           Issues with Route
15        launched app quoted mile home expected paid generally dozens times got picked later billed triple quote says confirmed change would ever could taken limo less dispute denied shut pay fired never  ...           Issues with Route
16   placed order eats food never showed charged anyways called tell customer service reps ignored food never showed eat lunch gave last money eat today